# Liquefaction Potential in Metro Manila due to 'The Big One M(7.2)'

## Declarations

In [1]:
import json
import time

import requests
import numpy as np
import pandas as pd
import geopandas as gpd
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import shapely.geometry

token = open("../assets/.mapbox_token").read()
px.set_mapbox_access_token(open("../assets/.mapbox_token").read())
pio.renderers.default = 'notebook'

## Data Collection

### Liquefaction Map

Source: 
* https://hazardhunter.georisk.gov.ph/map#

Data Preprocessing Tools: 
* https://earth.google.com
* https://qgis.org/en/site/

In [2]:
liqf_hp = gpd.read_file("../data/raw/liquefaction_hp.geojson")
liqf_mp = gpd.read_file("../data/raw/liquefaction_mp.geojson")
liqf_lp = gpd.read_file("../data/raw/liquefaction_lp.geojson")

In [3]:
liqf_map = pd.concat([liqf_hp, liqf_mp, liqf_lp]).reset_index(drop=True)

In [4]:
liqf_map.head()

Name  description  timestamp  begin  end  altitudeMode  tessellate  \
0  HP_1          NaN        NaN    NaN  NaN           NaN          -1   
1  HP_2          NaN        NaN    NaN  NaN           NaN          -1   
2  HP_3          NaN        NaN    NaN  NaN           NaN          -1   
3  HP_4          NaN        NaN    NaN  NaN           NaN          -1   
4  HP_5          NaN        NaN    NaN  NaN           NaN          -1   

   extrude  visibility  drawOrder  icon  \
0        0          -1        NaN   NaN   
1        0          -1        NaN   NaN   
2        0          -1        NaN   NaN   
3        0          -1        NaN   NaN   
4        0          -1        NaN   NaN   

                                            geometry  
0  POLYGON Z ((120.95267 14.65263 0.00000, 120.95...  
1  POLYGON Z ((120.93986 14.69246 0.00000, 120.93...  
2  POLYGON Z ((120.92697 14.73006 0.00000, 120.92...  
3  POLYGON Z ((121.08552 14.61446 0.00000, 121.08...  
4  POLYGON Z ((121.06247 14.48807 0.00000, 121.06...

In [5]:
liqf_map = liqf_map[['Name', 'geometry']]

In [6]:
liqf_map

Name                                           geometry
0   HP_1  POLYGON Z ((120.95267 14.65263 0.00000, 120.95...
1   HP_2  POLYGON Z ((120.93986 14.69246 0.00000, 120.93...
2   HP_3  POLYGON Z ((120.92697 14.73006 0.00000, 120.92...
3   HP_4  POLYGON Z ((121.08552 14.61446 0.00000, 121.08...
4   HP_5  POLYGON Z ((121.06247 14.48807 0.00000, 121.06...
5   HP_6  POLYGON Z ((120.95678 14.65363 0.00000, 120.95...
6   MP_1  POLYGON Z ((120.93550 14.73303 0.00000, 120.93...
7   MP_2  POLYGON Z ((120.94375 14.73342 0.00000, 120.94...
8   MP_3  POLYGON Z ((120.96554 14.67871 0.00000, 120.96...
9   MP_4  POLYGON Z ((121.01390 14.55771 0.00000, 121.01...
10  MP_5  POLYGON Z ((121.08705 14.61246 0.00000, 121.08...
11  MP_6  POLYGON Z ((121.10380 14.62656 0.00000, 121.10...
12  MP_7  POLYGON Z ((120.93860 14.69392 0.00000, 120.93...
13  MP_8  POLYGON Z ((120.94919 14.69045 0.00000, 120.94...
14  LP_1  POLYGON Z ((120.99365 14.65795 0.00000, 120.99...
15  LP_2  POLYGON Z ((120.96455 14.67246 0.00000, 120.96...
16  LP_3  POLYGON Z ((120.96440 14.71852 0.00000, 120.96...
17  LP_4  POLYGON Z ((120.96612 14.68566 0.00000, 120.96...
18  LP_5  POLYGON Z ((121.01591 14.59995 0.00000, 121.01...
19  LP_6  POLYGON Z ((121.00581 14.63101 0.00000, 121.00...

In [7]:
liqf_traces = []
colors = {'HP':'#f03b20', 'MP':'#feb24c', 'LP':'#ffeda0'}
legendgroup = {'HP':'High Potential', 'MP':'Moderate Potential', 'LP':'Low Potential'}

for area in liqf_map.iterrows():
    lons = list(area[1].geometry.exterior.coords.xy[0])
    lats = list(area[1].geometry.exterior.coords.xy[1])
    
    liqf_traces.append(go.Scattermapbox(
        fill = "toself",
        lon = lons, 
        lat = lats,
        marker = {'size': 5, 'color': colors[area[1].Name[:2]]},
        legendgroup= legendgroup[area[1].Name[:2]],
        legendgrouptitle_text= legendgroup[area[1].Name[:2]],
        name=area[1].Name,)
                     )
    
fig = go.Figure()
for trace in liqf_traces:
    fig.add_trace(trace)

fig.update_layout(
    margin ={'l':0,'t':0,'b':0,'r':0},
    mapbox = {
        'center': {'lon': 120.9787, 'lat': 14.5826},
        'style': "dark",
        'zoom': 10},
    mapbox_accesstoken=token,
    height=600,
    width=900,)
#     showlegend = False)

fig.show()

### Roadways lying on liquefiable areas

API Documentation:
* https://docs.ohsome.org/ohsome-api/development/endpoints.html#elements-extraction
* https://heigit.org/big-spatial-data-analytics-en/ohsome/
* https://www.openstreetmap.org/#map=15/14.5558/120.9999
* https://wiki.openstreetmap.org/wiki/Map_features#Highway

Extract all motorway roads within liquefaction area `hp_6`:

In [8]:
hp_6_coords = liqf_map.geometry.get_coordinates().loc[5]

In [9]:
hp_6_coords

x          y
5   120.956784  14.653632
5   120.957005  14.653539
5   120.957326  14.653381
5   120.957626  14.653186
5   120.957867  14.652785
..         ...        ...
5   120.956687  14.654257
5   120.956677  14.654126
5   120.956658  14.654010
5   120.956642  14.653797
5   120.956784  14.653632

[2084 rows x 2 columns]

In [10]:
bpolys = ",".join([str(coord.x) + "," + str(coord.y) for index, coord in hp_6_coords.iterrows()])

In [11]:
bpolys

'120.9567839159274,14.65363235311696,120.9570046912695,14.65353906728745,120.9573261324953,14.65338124201383,120.957625531167,14.65318618047039,120.9578670860718,14.65278516732276,120.9581580032214,14.65257055681041,120.9584408014604,14.65250152249477,120.958716990881,14.65243401149563,120.9590126783589,14.652204111343,120.9592219808755,14.6519975157508,120.9594810173302,14.65155865003795,120.9595714555023,14.65131481868773,120.9596235223909,14.65070532539352,120.9596081103752,14.64998637071479,120.9595827627833,14.64941026280165,120.9597202717473,14.64916990152748,120.9600931250471,14.6489221526847,120.9604530822548,14.6485145858126,120.9605169278757,14.64801765296836,120.9604766327912,14.64749411005963,120.9607931384684,14.64707233811767,120.9612371441733,14.64666342547926,120.9615860268463,14.64628092935058,120.9619861006449,14.64606643417319,120.9622067269526,14.64577395552073,120.9625048262012,14.64538155391423,120.9627882738573,14.64528430156375,120.9631652640251,14.6452060249423

In [31]:
URL = 'https://api.ohsome.org/v1/elements/geometry'
data = {"bpolys": bpolys, "time": "2023-09-24", "filter": "highway=motorway and type:way"}
response = requests.post(URL, data=data)
response.json()

{'attribution': {'url': 'https://ohsome.org/copyrights',
  'text': '© OpenStreetMap contributors'},
 'apiVersion': '1.10.1',
 'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'LineString',
    'coordinates': [[121.0035902, 14.5847067],
     [121.0037969, 14.5849267],
     [121.0040311, 14.5851757],
     [121.0059304, 14.5871961],
     [121.006072, 14.5873155],
     [121.006178, 14.5873992],
     [121.0067633, 14.5878389],
     [121.0069452, 14.5879792],
     [121.0071183, 14.5881254],
     [121.0072787, 14.588283],
     [121.0079816, 14.5890243],
     [121.0081687, 14.5892242],
     [121.0084529, 14.5895179]]},
   'properties': {'@osmId': 'way/688065629',
    '@snapshotTimestamp': '2023-09-24T00:00:00Z'}},
  {'type': 'Feature',
   'geometry': {'type': 'LineString',
    'coordinates': [[121.0015846, 14.5825336],
     [121.0025696, 14.5836211],
     [121.0031955, 14.5842869],
     [121.0035902, 14.5847067]]},
   'properties': {'@osmId': 'way/68806564

In [37]:
len(list(response.json().values())[3])

140

There are 140 motorways identified within `hp_6`.

In [38]:
list(response.json().values())[3][0]

{'type': 'Feature',
 'geometry': {'type': 'LineString',
  'coordinates': [[121.0035902, 14.5847067],
   [121.0037969, 14.5849267],
   [121.0040311, 14.5851757],
   [121.0059304, 14.5871961],
   [121.006072, 14.5873155],
   [121.006178, 14.5873992],
   [121.0067633, 14.5878389],
   [121.0069452, 14.5879792],
   [121.0071183, 14.5881254],
   [121.0072787, 14.588283],
   [121.0079816, 14.5890243],
   [121.0081687, 14.5892242],
   [121.0084529, 14.5895179]]},
 'properties': {'@osmId': 'way/688065629',
  '@snapshotTimestamp': '2023-09-24T00:00:00Z'}}

Determine all road ways within liquefaction areas:

In [ ]:
#This calculation may take some time to finish

highway_type = ["motorway", "trunk", "primary", "secondary", "tertiary", "unclassified", "residential"]

liquefaction_map_df = []
URL = 'https://api.ohsome.org/v1/elements/geometry'

liqf_df = liqf_map.set_index('Name')
liqf_coords = liqf_df.geometry.get_coordinates()

for name, coords in liqf_coords.groupby('Name'):
    bpolys = ",".join([str(coord.x) + "," + str(coord.y) for coord in coords.itertuples()])
    for highway in highway_type:
        data = {"bpolys": bpolys, "time": "2023-09-24", "filter": f"highway={highway} and type:way"}
        response = requests.post(URL, data=data)
        highway_gdf = gpd.GeoDataFrame.from_features(response.json())
        highway_gdf['type'] = highway
        liquefaction_map_df.append(highway_gdf)
        
        time.sleep(1)


In [13]:
liqf_roadways_gdf = gpd.read_file("../data/analytics/liqf_roadways_gdf.geojson", driver='GeoJSON')

In [14]:
liqf_roadways_gdf

type          @osmId  \
0            trunk    way/22747417   
1            trunk   way/820063539   
2            trunk   way/820063548   
3        secondary    way/23769397   
4        secondary    way/23769401   
...            ...             ...   
22394  residential  way/1202480860   
22395  residential  way/1202668629   
22396  residential  way/1202668639   
22397  residential  way/1202668640   
22398  residential  way/1204141855   

                                                geometry  
0      LINESTRING (120.95454 14.65374, 120.95436 14.6...  
1      LINESTRING (120.95470 14.65386, 120.95454 14.6...  
2      LINESTRING (120.95529 14.65434, 120.95470 14.6...  
3      LINESTRING (120.95177 14.65822, 120.95252 14.6...  
4      LINESTRING (120.95435 14.65447, 120.95369 14.6...  
...                                                  ...  
22394  LINESTRING (120.95160 14.67477, 120.95155 14.6...  
22395  LINESTRING (120.95012 14.67009, 120.95011 14.6...  
22396  LINESTRING (120.94994 14.66895, 120.94971 14.6...  
22397  LINESTRING (120.94945 14.66894, 120.94939 14.6...  
22398  LINESTRING (120.95004 14.66936, 120.95003 14.6...  

[22399 rows x 3 columns]

In [15]:
colors = {"motorway":"#33a02c", "trunk":"#e31a1c", "primary":"#1f78b4", "secondary":"#fdbf6f", 
          "tertiary":"#fb9a99", "unclassified":"#b2df8a", "residential":"#a6cee3"}
traces = []

for highway_type in liqf_roadways_gdf['type'].unique(): 
    gdf_by_type = liqf_roadways_gdf[liqf_roadways_gdf['type'] == highway_type]
    
    lats = []
    lons = []
    names = []
    
    for feature, name in zip(gdf_by_type.geometry, gdf_by_type['@osmId']):

        if isinstance(feature, shapely.geometry.linestring.LineString):
            linestrings = [feature]
        elif isinstance(feature, shapely.geometry.multilinestring.MultiLineString):
            linestrings = feature.geoms
        else:
            continue
            
        for linestring in linestrings:
            x, y = linestring.xy
            lats = np.append(lats, y)
            lons = np.append(lons, x)
            names = np.append(names, [name]*len(y))
            lats = np.append(lats, None)
            lons = np.append(lons, None)
            names = np.append(names, None)
            
    traces.append(go.Scattermapbox(
        mode = "lines",
        lon = lons,
        lat = lats,
        marker={'size':5, "color":colors[highway_type]},
        name=highway_type,
    ))

fig = go.Figure()
for trace in traces:
    fig.add_trace(trace)

fig.update_layout(
    margin ={'l':0,'t':0,'b':0,'r':0},
    mapbox = {
        'center': {'lon': 120.9787, 'lat': 14.5826},
        'style': "dark",
        'zoom': 10},
    mapbox_accesstoken=token,
    height=800,
    width=950,
    legend_title_text='Roadway Type')

fig.show()

### Hospitals and bed capacities at risk in liquefiable areas

In [16]:
ncr_hosp = gpd.read_file('../data/transformed/ncr_hosp.geojson')

In [17]:
ncr_hosp.head()

facility_name service_capability bed_capacity  \
0       A. ZARATE GENERAL HOSPITAL            Level 1           17   
1         ACEBEDO GENERAL HOSPITAL            Level 1           16   
2  ADVENTIST MEDICAL CENTER MANILA            Level 3          150   
3       AIR FORCE GENERAL HOSPITAL            Level 2          100   
4           ALABANG MEDICAL CENTER            Level 1           18   

   hospital_index                    geometry  
0            1691  POINT (120.98052 14.46901)  
1            1692  POINT (121.00509 14.71877)  
2            1693  POINT (120.99527 14.55595)  
3            1694  POINT (121.02001 14.51689)  
4            1695  POINT (121.02448 14.42777)

In [18]:
ncr_hosp.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 155 entries, 0 to 154
Data columns (total 5 columns):
 #   Column              Non-Null Count  Dtype   
---  ------              --------------  -----   
 0   facility_name       155 non-null    object  
 1   service_capability  155 non-null    object  
 2   bed_capacity        155 non-null    object  
 3   hospital_index      155 non-null    int64   
 4   geometry            155 non-null    geometry
dtypes: geometry(1), int64(1), object(3)
memory usage: 6.2+ KB


In [19]:
ncr_hosp['bed_capacity'] = ncr_hosp['bed_capacity'].astype(str).str.replace(',', '').astype(int)

In [20]:
liqf_hosp_contains = gpd.sjoin(liqf_map,
                               ncr_hosp,
                               how='left',
                               predicate='contains'
                              )

C:\Anaconda\lib\site-packages\pandas\core\reshape\merge.py:1204: RuntimeWarning:

invalid value encountered in cast



In [21]:
liqf_hosp_contains

Name                                           geometry  index_right  \
0   HP_1  POLYGON Z ((120.95267 14.65263 0.00000, 120.95...         86.0   
1   HP_2  POLYGON Z ((120.93986 14.69246 0.00000, 120.93...          NaN   
2   HP_3  POLYGON Z ((120.92697 14.73006 0.00000, 120.92...        118.0   
2   HP_3  POLYGON Z ((120.92697 14.73006 0.00000, 120.92...        119.0   
2   HP_3  POLYGON Z ((120.92697 14.73006 0.00000, 120.92...         11.0   
..   ...                                                ...          ...   
17  LP_4  POLYGON Z ((120.96612 14.68566 0.00000, 120.96...          NaN   
18  LP_5  POLYGON Z ((121.01591 14.59995 0.00000, 121.01...        144.0   
18  LP_5  POLYGON Z ((121.01591 14.59995 0.00000, 121.01...         28.0   
18  LP_5  POLYGON Z ((121.01591 14.59995 0.00000, 121.01...         77.0   
19  LP_6  POLYGON Z ((121.00581 14.63101 0.00000, 121.00...          NaN   

                                        facility_name service_capability  \
0                                  OSPITAL NG MALABON            Level 1   
1                                                 NaN                NaN   
2    SAN LORENZO HOSPITAL HEALTH MANAGEMENT CO., INC.            Level 1   
2                   SAN LORENZO RUIZ GENERAL HOSPITAL            Level 1   
2   ALLIED CARE EXPERTS (ACE) MEDICAL CENTER VALEN...            Level 2   
..                                                ...                ...   
17                                                NaN                NaN   
18  University of the East Ramon Magsaysay Memoria...            Level 3   
18                       DE LOS SANTOS MEDICAL CENTER            Level 3   
18                       NATIONAL CHILDREN'S HOSPITAL            Level 3   
19                                                NaN                NaN   

    bed_capacity  hospital_index  
0           34.0          1777.0  
1            NaN             NaN  
2           18.0          1809.0  
2           10.0          1810.0  
2          102.0          1702.0  
..           ...             ...  
17           NaN             NaN  
18         307.0          1835.0  
18         150.0          1719.0  
18         250.0          1768.0  
19           NaN             NaN  

[82 rows x 7 columns]

In [22]:
legendgroup = {'HP':'High Potential', 'MP':'Moderate Potential', 'LP':'Low Potential'}
liqf_hosp_contains['type'] = liqf_hosp_contains['Name'].apply(lambda x: legendgroup[x[:2]])
liqf_hosp_contains = liqf_hosp_contains.dropna()
liqf_hosp_contains['bed_capacity'] = liqf_hosp_contains['bed_capacity'].astype(int)

C:\Anaconda\lib\site-packages\geopandas\geodataframe.py:1543: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [23]:
liqf_hosp_contains

Name                                           geometry  index_right  \
0   HP_1  POLYGON Z ((120.95267 14.65263 0.00000, 120.95...         86.0   
2   HP_3  POLYGON Z ((120.92697 14.73006 0.00000, 120.92...        118.0   
2   HP_3  POLYGON Z ((120.92697 14.73006 0.00000, 120.92...        119.0   
2   HP_3  POLYGON Z ((120.92697 14.73006 0.00000, 120.92...         11.0   
3   HP_4  POLYGON Z ((121.08552 14.61446 0.00000, 121.08...        124.0   
..   ...                                                ...          ...   
15  LP_2  POLYGON Z ((120.96455 14.67246 0.00000, 120.96...         93.0   
16  LP_3  POLYGON Z ((120.96440 14.71852 0.00000, 120.96...        147.0   
18  LP_5  POLYGON Z ((121.01591 14.59995 0.00000, 121.01...        144.0   
18  LP_5  POLYGON Z ((121.01591 14.59995 0.00000, 121.01...         28.0   
18  LP_5  POLYGON Z ((121.01591 14.59995 0.00000, 121.01...         77.0   

                                        facility_name service_capability  \
0                                  OSPITAL NG MALABON            Level 1   
2    SAN LORENZO HOSPITAL HEALTH MANAGEMENT CO., INC.            Level 1   
2                   SAN LORENZO RUIZ GENERAL HOSPITAL            Level 1   
2   ALLIED CARE EXPERTS (ACE) MEDICAL CENTER VALEN...            Level 2   
3                         ST. CAMILLUS MEDICAL CENTER            Level 2   
..                                                ...                ...   
15                   OUR LADY OF GRACE HOSPITAL, INC.            Level 1   
16  VALENZUELA CITICARE MEDICAL CENTER TIMOG HILAG...            Level 2   
18  University of the East Ramon Magsaysay Memoria...            Level 3   
18                       DE LOS SANTOS MEDICAL CENTER            Level 3   
18                       NATIONAL CHILDREN'S HOSPITAL            Level 3   

    bed_capacity  hospital_index            type  
0             34          1777.0  High Potential  
2             18          1809.0  High Potential  
2             10          1810.0  High Potential  
2            102          1702.0  High Potential  
3             40          1815.0  High Potential  
..           ...             ...             ...  
15            28          1784.0   Low Potential  
16            40          1838.0   Low Potential  
18           307          1835.0   Low Potential  
18           150          1719.0   Low Potential  
18           250          1768.0   Low Potential  

[74 rows x 8 columns]

In [24]:
liqf_potential_hosp = liqf_hosp_contains.groupby(['type','service_capability'])['facility_name'].count().reset_index()

liqf_potential_hosp["type"] = pd.Categorical(liqf_potential_hosp["type"], 
                                             ["High Potential", "Moderate Potential", "Low Potential"])
liqf_potential_hosp = liqf_potential_hosp.sort_values("type").reset_index(drop=True)



In [25]:
liqf_potential_hosp

type service_capability  facility_name
0      High Potential            Level 1             20
1      High Potential            Level 2             12
2      High Potential            Level 3             21
3  Moderate Potential            Level 1              7
4  Moderate Potential            Level 2              3
5  Moderate Potential            Level 3              5
6       Low Potential            Level 1              2
7       Low Potential            Level 2              1
8       Low Potential            Level 3              3

In [26]:
fig = px.bar(liqf_potential_hosp, 
             x="facility_name", 
             y="service_capability",
             color="type", barmode="group",
             labels={
                "type": "Liquefaction Potential",
                "facility_name": "No. of Hospitals",
                "service_capability":"Service Capability"},
             color_discrete_map={'High Potential':'#f03b20',
                   'Moderate Potential':'#feb24c', 
                   'Low Potential':'#ffeda0'},  
             title="Hospitals Lying on Liquefiable Areas")

fig.update_yaxes(autorange="reversed")

fig.update_layout(plot_bgcolor='white')
fig.update_layout(legend=dict(
    orientation="h",
    yanchor="bottom",
    y=1.02,
    xanchor="right",
    x=1
))

fig.show()

In [27]:
liqf_potential_capacity = liqf_hosp_contains.groupby(['type'])['bed_capacity'].sum().reset_index()

In [28]:
liqf_potential_capacity = liqf_potential_capacity.sort_values("bed_capacity", ascending=False).reset_index(drop=True)
liqf_potential_capacity

type  bed_capacity
0      High Potential          9286
1  Moderate Potential          1776
2       Low Potential           857

In [29]:
fig = px.bar(liqf_potential_capacity, 
             x="bed_capacity", 
             y="type", 
             color="type",
             labels={
                "type": "Liquefaction Potential",
                "bed_capacity": "Bed Capacity",},
             color_discrete_map={'High Potential':'#f03b20', 
                                 'Moderate Potential':'#feb24c', 
                                 'Low Potential':'#ffeda0'},
              title="Bed Capacities Lying on Liquefiable Areas")

fig.update_layout(plot_bgcolor='white', showlegend=False)

fig.show()

## Data Review and Export


#### Liquefaction Map

In [118]:
legendgroup = {'HP':'High Potential', 'MP':'Moderate Potential', 'LP':'Low Potential'}
liqf_map['potential'] = liqf_map['Name'].apply(lambda x: legendgroup[x[:2]])

In [120]:
liqf_map.head()

Name                                           geometry       potential
0  HP_1  POLYGON Z ((120.95267 14.65263 0.00000, 120.95...  High Potential
1  HP_2  POLYGON Z ((120.93986 14.69246 0.00000, 120.93...  High Potential
2  HP_3  POLYGON Z ((120.92697 14.73006 0.00000, 120.92...  High Potential
3  HP_4  POLYGON Z ((121.08552 14.61446 0.00000, 121.08...  High Potential
4  HP_5  POLYGON Z ((121.06247 14.48807 0.00000, 121.06...  High Potential

In [121]:
#liqf_map.to_file("../data/analytics/liquefaction_map.geojson", driver="GeoJSON")

#### NCR hospitals

In [157]:
ncr_hosp = ncr_hosp.sjoin(liqf_map,
              how='left',
              predicate='within')

C:\Anaconda\lib\site-packages\pandas\core\reshape\merge.py:1204: RuntimeWarning:

invalid value encountered in cast



In [158]:
ncr_hosp['potential'] = ncr_hosp['potential'].fillna('No Potential')

In [160]:
ncr_hosp = ncr_hosp.drop(['index_right', 'Name'], axis=1)

In [165]:
ncr_hosp = ncr_hosp.drop_duplicates('facility_name')

In [167]:
ncr_hosp.head()

facility_name service_capability  bed_capacity  \
0       A. ZARATE GENERAL HOSPITAL            Level 1            17   
1         ACEBEDO GENERAL HOSPITAL            Level 1            16   
2  ADVENTIST MEDICAL CENTER MANILA            Level 3           150   
3       AIR FORCE GENERAL HOSPITAL            Level 2           100   
4           ALABANG MEDICAL CENTER            Level 1            18   

   hospital_index                    geometry       potential  
0            1691  POINT (120.98052 14.46901)    No Potential  
1            1692  POINT (121.00509 14.71877)    No Potential  
2            1693  POINT (120.99527 14.55595)  High Potential  
3            1694  POINT (121.02001 14.51689)    No Potential  
4            1695  POINT (121.02448 14.42777)    No Potential

In [168]:
#ncr_hosp.to_file('../data/analytics/ncr_hosp.geojson', driver='GeoJSON')

#### Travel Matrix

In [173]:
travel_matrix = pd.read_csv('../data/transformed/travel_matrix.csv', index_col=0)

In [176]:
travel_matrix = travel_matrix.rename({"barangay":"barangay_index", "hospital":"hospital_index"}, axis=1)

In [177]:
travel_matrix

barangay_index  hospital_index  duration
0                 0            1691   2367.47
1                 1            1691   2271.67
2                 2            1691   2263.77
3                 3            1691   2230.33
4                 4            1691   2212.23
..              ...             ...       ...
150            1690            1841   2116.04
151            1690            1842   2396.09
152            1690            1843   2732.35
153            1690            1844   1785.05
154            1690            1845   2292.73

[262105 rows x 3 columns]

In [179]:
travel_matrix = pd.merge(travel_matrix,
                         ncr_hosp[['hospital_index', 'potential']],
                         on='hospital_index',
                         how='left')

In [180]:
travel_matrix

barangay_index  hospital_index  duration       potential
0                    0            1691   2367.47    No Potential
1                    1            1691   2271.67    No Potential
2                    2            1691   2263.77    No Potential
3                    3            1691   2230.33    No Potential
4                    4            1691   2212.23    No Potential
...                ...             ...       ...             ...
262100            1690            1841   2116.04    No Potential
262101            1690            1842   2396.09    No Potential
262102            1690            1843   2732.35  High Potential
262103            1690            1844   1785.05    No Potential
262104            1690            1845   2292.73    No Potential

[262105 rows x 4 columns]

In [181]:
#travel_matrix.to_csv("../data/analytics/travel_matrix.csv")

---